# CTA 2.0

In [1]:
import pandas as pd
import numpy as np

from tinycta.port import build_portfolio

In [2]:
# Load prices
prices = pd.read_csv("data/Prices_hashed.csv", index_col=0, parse_dates=True).ffill()

In [3]:
# take two moving averages and apply the sign-function, adjust by volatility
def f(price, fast=32, slow=96, volatility=32):
    s = price.ewm(com=slow, min_periods=300).mean()
    f = price.ewm(com=fast, min_periods=300).mean()
    std = price.pct_change().ewm(com=volatility, min_periods=300).std()
    return np.sign(f-s)/std

In [4]:
from ipywidgets import Label, HBox, VBox, IntSlider

fast = IntSlider(min=4, max=192, step=4, value=32)
slow = IntSlider(min=4, max=192, step=4, value=96)
vola = IntSlider(min=4, max=192, step=4, value=32)
left_box = VBox([Label("Fast Moving Average"), Label("Slow Moving Average"), Label("Volatility")])
right_box = VBox([fast, slow, vola])
HBox([left_box, right_box])

In [5]:
portfolio = build_portfolio(prices=prices, cashposition=1e6*
                            f(prices, fast=fast.value, slow=slow.value, volatility=vola.value),
                           aum=1e9)

/tmp/ipykernel_1188603/847244084.py:5: FutureWarning: The default fill_method='pad' in DataFrame.pct_change is deprecated and will be removed in a future version. Call ffill before calling pct_change to retain current behavior and silence this warning.
  std = price.pct_change().ewm(com=volatility, min_periods=300).std()


* This is a **univariate** trading system, we map the (real) price of an asset to its (cash)position
* Only 3 **free parameters** used here.
* Only 4 lines of code
* Scaling the bet-size by volatility has improved the situation.

Results do not look terrible but...
* No concept of risk integrated 

Often hedge funds outsource the risk management to some board or committee
and develop machinery for more systematic **parameter-hacking**.

In [6]:
portfolio.plot()

In [7]:
portfolio.metrics()

{'Sharpe': 0.8645763036278685,
 'Kurtosis': 6.4416133709939825,
 'Skewness': -0.41280705641739607,
 'Annualized Volatility (%)': 17.80008576897475,
 'Annualized Return (%)': 15.389532358399215}